Final Project(Data collection & Data wrangling)

In [1]:
import requests
import pandas as pd


In [31]:
# getting data from api
from pandas import json_normalize
api_url = "http://api.nobelprize.org/2.0/nobelPrizes?"

def fetch_data(url, params):
    try:
        response = requests.get(url, params)
        response.raise_for_status()
        return response.json()
    except requests.RequestException as e:
        print(f"error while fetching the data {url}: {e}")
        return None

params ={"offset":"1",
         "limit":"1500",
         "sort":"asc",
         "nobelPrizeYear":"1901",
         "yearTo":"2024",
         "format": "json"}
nobel_prize = fetch_data(api_url, params)

if nobel_prize:
    df2 = json_normalize(nobel_prize['nobelPrizes'])
    df2 = df2.drop(['category.no', 'category.se', 'categoryFullName.no', 'categoryFullName.se', 'links.rel', 'topMotivation.en', 'topMotivation.se', 'links.href', 'links.action', 'links.types'], axis = 1)
    df2 = df2.explode('laureates').reset_index(drop=True)
    print(df2['laureates'].head())
    df2 = df2[df2['laureates'].notnull()]
    df2['winner_id'] = df2['laureates'].apply(lambda x: x['id'])
    df2['winner_link'] = df2['laureates'].apply(lambda x: x['links']['href'])
    df2 = df2.drop(columns=['laureates'])
    print(df2.head)
    print(df2.winner_id.nunique())


0    {'id': '569', 'knownName': {'en': 'Sully Prudh...
1    {'id': '462', 'knownName': {'en': 'Henry Dunan...
2    {'id': '463', 'knownName': {'en': 'Frédéric Pa...
3    {'id': '1', 'knownName': {'en': 'Wilhelm Conra...
4    {'id': '293', 'knownName': {'en': 'Emil von Be...
Name: laureates, dtype: object
<bound method NDFrame.head of      awardYear dateAwarded  prizeAmount  prizeAmountAdjusted  \
0         1901  1901-11-14       150782              9704878   
1         1901  1901-12-10       150782              9704878   
2         1901  1901-12-10       150782              9704878   
3         1901  1901-11-12       150782              9704878   
4         1901  1901-10-30       150782              9704878   
...        ...         ...          ...                  ...   
1055      2024  2024-10-11     11000000             11000000   
1056      2024  2024-10-08     11000000             11000000   
1057      2024  2024-10-08     11000000             11000000   
1058      2024  2024-10-

In [32]:
# getting laureates data from api 
from time import sleep
data_list = []
for url in df2['winner_link']:
    data = fetch_data(url, "")
    if data:
        print("Fetching ", data)
        for item in data:
            print("Fetching ", item)
            data_list.append({
                "id": item.get('id'),
                "given_name": item.get('givenName', {}).get('en') if isinstance(item.get('givenName'), dict) else item.get('nativeName', {}),
                "family_name": item.get('familyName', {}).get('en') if isinstance(item.get('familyName'), dict) else item.get('nativeName', {}),
                "full_name": item.get('fullName', {}).get('en') if isinstance(item.get('fullName'), dict) else item.get('nativeName', {}),
                "gender": item.get('gender'),
                "birth_date": item.get('birth', {}).get('date'),
                "birth_place_city": item.get('birth', {}).get('place', {}).get('city', {}).get('en') if isinstance(item.get('birth', {}).get('place', {}).get('city'), dict) else None,
                "birth_place_country": item.get('birth', {}).get('place', {}).get('country', {}).get('en') if isinstance(item.get('birth', {}).get('place', {}).get('country'), dict) else item.get('foundedCountry', {}).get('en'),
                "city_now": item.get('birth', {}).get('place', {}).get('cityNow', {}).get('en') if isinstance(item.get('birth', {}).get('place', {}).get('cityNow'), dict) else None,
                "country_now": item.get('birth', {}).get('place', {}).get('countryNow', {}).get('en') if isinstance(item.get('birth', {}).get('place', {}).get('countryNow'), dict) else item.get('foundedCountryNow', {}).get('en'),
                "continent": item.get('birth', {}).get('place', {}).get('continent', {}).get('en') if isinstance(item.get('birth', {}).get('place', {}).get('continent'), dict) else item.get('foundedContinent', {}).get('en')
            })
    #sleep(5)

winners = pd.DataFrame(data_list)
print(winners)


Fetching  [{'id': '569', 'knownName': {'en': 'Sully Prudhomme', 'se': 'Sully Prudhomme'}, 'givenName': {'en': 'Sully', 'se': 'Sully'}, 'familyName': {'en': 'Prudhomme', 'se': 'Prudhomme'}, 'fullName': {'en': 'Sully Prudhomme', 'se': 'Sully Prudhomme'}, 'penName': '(pen-name of René François Armand Prudhomme)', 'penNameOf': {'fullName': 'René François Armand Prudhomme'}, 'fileName': 'prudhomme', 'gender': 'male', 'birth': {'date': '1839-03-16', 'place': {'city': {'en': 'Paris', 'no': 'Paris', 'se': 'Paris'}, 'country': {'en': 'France', 'no': 'Frankrike', 'se': 'Frankrike'}, 'cityNow': {'en': 'Paris', 'no': 'Paris', 'se': 'Paris', 'sameAs': ['https://www.wikidata.org/wiki/Q90', 'https://www.wikipedia.org/wiki/Paris'], 'latitude': '48.860093', 'longitude': '2.355954'}, 'countryNow': {'en': 'France', 'no': 'Frankrike', 'se': 'Frankrike', 'sameAs': ['https://www.wikidata.org/wiki/Q142'], 'latitude': '47.000000', 'longitude': '2.000000'}, 'continent': {'en': 'Europe', 'no': 'Europa', 'se': '

In [38]:
# saving the data to csv
df_combined = pd.merge(df2, winners, left_on='winner_id', right_on='id', how='inner')
df_combined.to_csv('Final Project/nobel_prize.csv', index=False)



In [2]:
# getting additional data from world bank
gdp_and_population = pd.read_csv('Final Project/GDP and population_Data.csv')
gdp_and_population.head()

Country Name Country Code  \
0  Afghanistan          AFG   
1  Afghanistan          AFG   
2  Afghanistan          AFG   
3  Afghanistan          AFG   
4      Albania          ALB   

                                         Series Name        Series Code  \
0                       GDP per capita (current US$)     NY.GDP.PCAP.CD   
1  Government expenditure on education, total (% ...  SE.XPD.TOTL.GD.ZS   
2    Research and development expenditure (% of GDP)  GB.XPD.RSDV.GD.ZS   
3                                  Population, total        SP.POP.TOTL   
4                       GDP per capita (current US$)     NY.GDP.PCAP.CD   

  1960 [YR1960] 1961 [YR1961] 1962 [YR1962] 1963 [YR1963] 1964 [YR1964]  \
0            ..            ..            ..            ..            ..   
1            ..            ..            ..            ..            ..   
2            ..            ..            ..            ..            ..   
3       8622466       8790140       8969047       9157465       9355514   
4            ..            ..            ..            ..            ..   

  1965 [YR1965]  ...     2014 [YR2014]     2015 [YR2015]     2016 [YR2016]  \
0            ..  ...  626.512929086139  566.881129708434  523.053011984748   
1            ..  ...  3.69521999359131   3.2558000087738  4.54397010803223   
2            ..  ...                ..                ..                ..   
3       9565147  ...          32716210          33753499          34636207   
4            ..  ...  4578.63320812155  3952.80357364813  4124.05538986272   

      2017 [YR2017]     2018 [YR2018]     2019 [YR2019]     2020 [YR2020]  \
0  526.140801025756  492.090630986151  497.741431256813  512.055098005672   
1  4.34319019317627                ..                ..                ..   
2                ..                ..                ..                ..   
3          35643418          36686784          37769499          38972230   
4  4531.03220675893  5287.66080067575   5396.2142432843   5343.0377039956   

      2021 [YR2021]     2022 [YR2022]     2023 [YR2023]  
0  355.777826392648  352.603733092107                ..  
1                ..                ..                ..  
2                ..                ..                ..  
3          40099462          41128771          42239854  
4  6377.20309553753  6810.11404104233  8367.77573143421  

[5 rows x 68 columns]

In [3]:
#  turning years from columns to rows (from wide data to long)
long_df = pd.melt(gdp_and_population, id_vars=['Country Name', 'Country Code', 'Series Name', 'Series Code'], var_name='Year', value_name='Value')
long_df['Year'] = long_df['Year'].str.replace(r' \[YR\d+\]', '', regex=True)
long_df['Value'] = pd.to_numeric(long_df['Value'], errors='coerce')
long_df.drop('Series Code', axis=1, inplace=True)
long_df.head()

Country Name Country Code  \
0  Afghanistan          AFG   
1  Afghanistan          AFG   
2  Afghanistan          AFG   
3  Afghanistan          AFG   
4      Albania          ALB   

                                         Series Name  Year      Value  
0                       GDP per capita (current US$)  1960        NaN  
1  Government expenditure on education, total (% ...  1960        NaN  
2    Research and development expenditure (% of GDP)  1960        NaN  
3                                  Population, total  1960  8622466.0  
4                       GDP per capita (current US$)  1960        NaN

In [5]:
# pivoting the data from long to wide 
# getting new columns from Series Name
wide_df = pd.pivot_table(long_df, index=['Country Name', 'Country Code', 'Year'], columns='Series Name', values='Value').reset_index()
wide_df.head()




Series Name Country Name Country Code  Year  GDP per capita (current US$)  \
0            Afghanistan          AFG  1960                           NaN   
1            Afghanistan          AFG  1961                           NaN   
2            Afghanistan          AFG  1962                           NaN   
3            Afghanistan          AFG  1963                           NaN   
4            Afghanistan          AFG  1964                           NaN   

Series Name  Government expenditure on education, total (% of GDP)  \
0                                                          NaN       
1                                                          NaN       
2                                                          NaN       
3                                                          NaN       
4                                                          NaN       

Series Name  Population, total  \
0                    8622466.0   
1                    8790140.0   
2                    8969047.0   
3                    9157465.0   
4                    9355514.0   

Series Name  Research and development expenditure (% of GDP)  
0                                                        NaN  
1                                                        NaN  
2                                                        NaN  
3                                                        NaN  
4                                                        NaN

In the World Bank data, the country column includes groups of countries, which creates additional data that does not match the countries in the Nobel Prize data. For this reason, I downloaded the unique country names from this repository https://github.com/umpirsky/country-list/blob/master/data/en_US/country.csv to exclude the groups of countries.

In [11]:

countries = pd.read_csv('Final Project/country.csv')
countries.head()

id           value
0  AF     Afghanistan
1  AX   Åland Islands
2  AL         Albania
3  DZ         Algeria
4  AS  American Samoa

In [17]:
#getting data without groups of countries
wide_df_corr = pd.merge(
    wide_df,
    countries,
    left_on=['Country Name'],   
    right_on=['value'], 
    how='inner'                              
)

wide_df_corr.head()



#wide_df_corr = wide_df_corr.dropna()
wide_df_corr.describe()
wide_df_corr.info()
wide_df_corr.shape

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 11456 entries, 0 to 11455
Data columns (total 9 columns):
 #   Column                                                 Non-Null Count  Dtype  
---  ------                                                 --------------  -----  
 0   Country Name                                           11456 non-null  object 
 1   Country Code                                           11456 non-null  object 
 2   Year                                                   11456 non-null  int64  
 3   GDP per capita (current US$)                           9497 non-null   float64
 4   Government expenditure on education, total (% of GDP)  4442 non-null   float64
 5   Population, total                                      11456 non-null  float64
 6   Research and development expenditure (% of GDP)        1955 non-null   float64
 7   id                                                     11392 non-null  object 
 8   value                                          

(11456, 9)

In [18]:
nobel_prize= pd.read_csv('Final Project/nobel_prize.csv')
nobel_prize.head()

awardYear dateAwarded  prizeAmount  prizeAmountAdjusted  \
0       1901  1901-11-14       150782              9704878   
1       1901  1901-12-10       150782              9704878   
2       1901  1901-12-10       150782              9704878   
3       1901  1901-11-12       150782              9704878   
4       1901  1901-10-30       150782              9704878   

              category.en                        categoryFullName.en  \
0              Literature              The Nobel Prize in Literature   
1                   Peace                      The Nobel Peace Prize   
2                   Peace                      The Nobel Peace Prize   
3                 Physics                 The Nobel Prize in Physics   
4  Physiology or Medicine  The Nobel Prize in Physiology or Medicine   

   winner_id                                winner_link   id      given_name  \
0        569  https://api.nobelprize.org/2/laureate/569  569           Sully   
1        462  https://api.nobelprize.org/2/laureate/462  462           Henry   
2        463  https://api.nobelprize.org/2/laureate/463  463        Frédéric   
3          1    https://api.nobelprize.org/2/laureate/1    1  Wilhelm Conrad   
4        293  https://api.nobelprize.org/2/laureate/293  293            Emil   

   family_name               full_name gender  birth_date birth_place_city  \
0    Prudhomme         Sully Prudhomme   male  1839-03-16            Paris   
1       Dunant       Jean Henry Dunant   male  1828-05-08           Geneva   
2        Passy          Frédéric Passy   male  1822-05-20            Paris   
3      Röntgen  Wilhelm Conrad Röntgen   male  1845-03-27           Lennep   
4  von Behring  Emil Adolf von Behring   male  1854-03-15         Hansdorf   

  birth_place_country   city_now  country_now continent  
0              France      Paris       France    Europe  
1         Switzerland     Geneva  Switzerland    Europe  
2              France      Paris       France    Europe  
3             Prussia  Remscheid      Germany    Europe  
4             Prussia     Lawice       Poland    Europe

In [19]:
#merging nobel prize data with country and gdp and population data
nobel_prize['awardYear'] = nobel_prize['awardYear'].astype(int)
wide_df['Year'] = wide_df['Year'].astype(int)
merged_df = pd.merge(
    wide_df_corr,
    nobel_prize,
    left_on=['Country Name', 'Year'],   
    right_on=['birth_place_country', 'awardYear'], 
    how='left'                              
)

merged_df.head()

merged_df.describe()
merged_df.info()
merged_df.to_csv('Final Project/nobel_prize_gdp_pop_exp.csv', index=False)
merged_df.shape

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 11525 entries, 0 to 11524
Data columns (total 28 columns):
 #   Column                                                 Non-Null Count  Dtype  
---  ------                                                 --------------  -----  
 0   Country Name                                           11525 non-null  object 
 1   Country Code                                           11525 non-null  object 
 2   Year                                                   11525 non-null  int64  
 3   GDP per capita (current US$)                           9566 non-null   float64
 4   Government expenditure on education, total (% of GDP)  4483 non-null   float64
 5   Population, total                                      11525 non-null  float64
 6   Research and development expenditure (% of GDP)        1981 non-null   float64
 7   id_x                                                   11461 non-null  object 
 8   value                                         

(11525, 28)